In [408]:
import copy

import torch
from torch import nn
from torch.utils.data import DataLoader
#from tqdm.notebook import tqdm, trange
from tqdm import tqdm, trange
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from copy import deepcopy

In [409]:
X = pd.read_csv("data/train_right_time.csv")
X = X.drop(['Time'],axis=1)
X = X.drop(['Unnamed: 0'],axis=1)


#train_tensor = torch.tensor(train.values)
Y = pd.read_csv('data/check_right_time.csv')
Y = Y.drop(['Unnamed: 0'],axis=1)
Y = Y.drop(['Unnamed: 0.1'],axis=1)
Y = Y.drop(['ts'],axis=1)

X = X.to_numpy()
Y = Y.to_numpy()

In [410]:

scalerX = preprocessing.StandardScaler().fit(X)
X = scalerX.transform(X)
scalerY = preprocessing.StandardScaler().fit(Y)
Y = scalerY.transform(Y)

In [411]:
ds = pd.DataFrame(Y)
ds.max()

0     6.535743
1    12.977597
2    11.658765
3     6.445493
4     8.063977
dtype: float64

In [412]:

X_train, X_test, y_train, y_test = train_test_split(X, Y, random_state=42, test_size=0.15)

#train = pd.DataFrame(columns=['X','Y'])
#test = pd.DataFrame(columns=['X','Y'])
test = []
train = []

"""
for X, Y in tqdm(zip(X_train.iterrows(), y_train.iterrows()), total=X_train.shape[0]):
    train.loc[len(train.index)]=(np.array(X),np.array(Y))

for X, Y in tqdm(zip(X_test.iterrows(), y_test.iterrows()), total=X_test.shape[0]):
    train.loc[len(test.index)]=(np.array(X),np.array(Y))
"""

for X, Y in tqdm(zip(X_train, y_train), total=X_train.shape[0]):
    train.append((X,Y))
for X, Y in tqdm(zip(X_test, y_test), total=X_test.shape[0]):
    test.append((X,Y))

#test = test.to_numpy()
#train = train.to_numpy()


#test_tensor = torch.tensor(test.values)

100%|██████████| 1825/1825 [00:00<00:00, 455821.16it/s]


In [413]:
#test = torch.tensor(test)
#train = torch.tensor(train)

In [414]:
batch_size = 50

# Create data loaders.
test = DataLoader(test, batch_size=batch_size, shuffle=True)
train = DataLoader(train, batch_size=batch_size, shuffle=True)

for X, y in test:
    print(f"Shape of X : {X.shape}")
    print(f"Shape of y: {y.shape} {y.dtype}")
    break

Shape of X : torch.Size([50, 33])
Shape of y: torch.Size([50, 5]) torch.float64


In [415]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

# Define model
class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        # take in input resistance, age, heater_r and heater_V
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(33, 16),
            nn.LeakyReLU(),
            nn.Linear(16, 16),
            nn.LeakyReLU(),
            nn.Linear(16, 5),
        )

        self.input_channel = nn.Linear


    def forward(self, x):
        #x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits

model = NeuralNetwork().to(device)
print(model)

Using cpu device
NeuralNetwork(
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (linear_relu_stack): Sequential(
    (0): Linear(in_features=33, out_features=16, bias=True)
    (1): LeakyReLU(negative_slope=0.01)
    (2): Linear(in_features=16, out_features=16, bias=True)
    (3): LeakyReLU(negative_slope=0.01)
    (4): Linear(in_features=16, out_features=5, bias=True)
  )
)


In [416]:
loss_fn = nn.MSELoss()
loss_2 = nn.MSELoss()
#loss_fn = nn.L1Loss()
optimizer = torch.optim.SGD(model.parameters(), lr=1e-7, momentum=0.9)

In [417]:
def trainf(dataloader, model, loss_fn, optimizer):
    global best_model
    best_loss = float("inf")
    size = len(dataloader.dataset)
    model.double()
    model.train()
    for batch , (X, Y) in enumerate(dataloader):
        gas_loss = [([],[]) for _ in range(5)]
        X, Y = X.to(device), Y.to(device)
        loss = float("inf")
        optimizer.zero_grad()
        # Compute prediction error
        for x_line, y_line in zip(X, Y):
            pred = model(x_line)
            for i, (gas, y_lin) in enumerate(zip(pred, y_line)):
                gas_loss[i][0].append(y_lin)
                gas_loss[i][1].append(gas)
            loss = loss_fn(pred, y_line)
            loss.backward()
        # Backpropagation
        optimizer.step()

        if loss < best_loss:
            best_loss = loss
            best_model = deepcopy(model)

        if batch % 100 == 0:
            for i, gas in enumerate(gas_loss):
                pass
                #print(f"gas {i}: loss = {loss_2(torch.tensor(gas[0]), torch.tensor(gas[1])).item()}")
            loss, current = loss.item(), batch * len(X)
            print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")

In [418]:
def testf(dataloader, model, loss_fn):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        gas_avg_loss = [0 for _ in range(5)]
        for X, Y in dataloader:
            gas_loss = [([],[]) for _ in range(5)]
            X, Y = X.to(device), Y.to(device)
            for x_line, y_line in zip(X, Y):
                pred = model(x_line)
                for i, (gas, y_lin) in enumerate(zip(pred, y_line)):
                    gas_loss[i][0].append(y_lin)
                    gas_loss[i][1].append(gas)
                test_loss += loss_fn(pred, y_line).item()
                #correct += (pred.argmax(1) == y).type(torch.float).sum().item()
            for i, gas in enumerate(gas_loss):
                for yp, pre in zip(gas[0],gas[1]):
                    gas_avg_loss[i] += loss_2(torch.tensor(yp), torch.tensor(pre)).item()
    test_loss /= num_batches * batch_size
    for i, num in enumerate(gas_avg_loss):
        print(f'gas {i}: avg loss = {num / (num_batches * batch_size)}')
    #correct /= size
    #print(f"Test Error: \n Accuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f} \n")
    print(f"Test Error: \n Avg loss: {test_loss:>8f} \n")


In [419]:
epochs = 20
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    trainf(train, model, loss_fn, optimizer)
    testf(test, model, loss_fn)
print("Done!")

Epoch 1
-------------------------------
loss: 0.141936  [    0/10337]
loss: 0.240936  [ 5000/10337]
loss: 0.211599  [10000/10337]


C:\Users\samue\AppData\Local\Temp\ipykernel_9428\2339648106.py:20: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



gas 0: avg loss = 1.0180183248816466
gas 1: avg loss = 1.0516705934132808
gas 2: avg loss = 1.215230857998118
gas 3: avg loss = 1.0302523758897362
gas 4: avg loss = 0.963752812672395
Test Error: 
 Avg loss: 1.055785 

Epoch 2
-------------------------------
loss: 0.862852  [    0/10337]
loss: 0.326747  [ 5000/10337]
loss: 0.434261  [10000/10337]
gas 0: avg loss = 1.0175187667575996
gas 1: avg loss = 1.0505074108533585
gas 2: avg loss = 1.2151245950459626
gas 3: avg loss = 1.02983845116602
gas 4: avg loss = 0.963599560874802
Test Error: 
 Avg loss: 1.055318 

Epoch 3
-------------------------------
loss: 0.378372  [    0/10337]
loss: 0.287395  [ 5000/10337]
loss: 12.347845  [10000/10337]
gas 0: avg loss = 1.0170158419844428
gas 1: avg loss = 1.0493668408036707
gas 2: avg loss = 1.2150205996582089
gas 3: avg loss = 1.0294233101288364
gas 4: avg loss = 0.963448354899838
Test Error: 
 Avg loss: 1.054855 

Epoch 4
-------------------------------
loss: 0.543942  [    0/10337]
loss: 0.649704 

In [420]:
import plotly.express as px

In [421]:
for i in range(5):
    px.scatter(
        x = np.concatenate((y_train, y_test), axis = 0)[:,i],
        y = model(torch.tensor(np.concatenate((X_train, X_test), axis = 0))).detach().numpy()[:,i]
    ).show()

torch.save(model.state_dict(), "models/model_samu.pth")
print("Saved PyTorch Model State to model.pth")
model = NeuralNetwork()
model.load_state_dict(torch.load("models/model_samu.pth"))